In [1]:
import numpy as np
import plotly.graph_objects as go
from plyfile import PlyData
from plotly.offline import iplot
from plyfile import PlyData

import os
current_path = os.getcwd()

In [3]:
def load_off_file(file_path):
    with open(file_path, 'r') as file:
        lines = file.readlines()

    # Extracting information from the OFF file
    num_vertices, num_faces, _ = map(int, lines[1].split())
    vertices = np.array([list(map(float, line.split()[0:3])) for line in lines[2:2+num_vertices]])

    # Assuming faces are triangles for simplicity
    faces = np.array([list(map(int, line.split()[1:])) for line in lines[2+num_vertices:]])

    return vertices, faces

In [4]:
def load_ply_file(file_path):
    # Load PLY file
    ply_data = PlyData.read(file_path)

    # Extract vertex data
    vertices = np.array([(vertex['x'], vertex['y'], vertex['z']) for vertex in ply_data['vertex']])

    # Extract face data
    faces = np.array([list(face) for face in ply_data['face']['vertex_indices']])

    return vertices, faces

In [5]:
def load_txt_file(file_path):
    try:
        with open(file_path, 'r') as file:
            content = file.readlines()
            # Remove newline characters from each line
            content = [line.strip() for line in content]
        return content
    except FileNotFoundError:
        print(f"The file '{file_path}' was not found.")
        return None
    except Exception as e:
        print(f"An error occurred: {e}")
        return None

In [6]:
def read_obj_file(file_path):
    vertices = []
    faces = []

    with open(file_path, 'r') as obj_file:
        for line in obj_file:
            # Split the line into words
            words = line.split()

            if not words:
                continue

            # Check for vertex data
            if words[0] == 'v':
                vertex = list(map(float, words[1:]))
                vertices.append(vertex)

            # Check for face data
            elif words[0] == 'f':
                face = [int(vertex.split('/')[0]) for vertex in words[1:]]
                faces.append(face)

    return np.array(vertices), np.array(faces)

In [7]:
def show_3d_model(path_model, path_label=None):
    
    # Load models
    if path_model.endswith('ply'):
        vertices, faces = load_ply_file(path_model)
    elif path_model.endswith('off'):
        vertices, faces = load_off_file(path_model)
    elif path_model.endswith('obj'):
        vertices, faces = read_obj_file(path_model)

    # Load labels
    if path_label is not None:
        labels = load_txt_file(path_label)
        color_scale = {
            '0': 'black',
            '1': 'red',
            '2': 'blue',
            '3': 'green',
            '4': 'yellow',
            '5': 'purple',
            '6': 'orange',
            '7': 'pink',
            '8': 'cyan'}
        face_colors = [color_scale[label] for row in labels for label in row]
        print(len(labels),len(faces))
        
        # Extract x, y, z coordinates from vertices
        x, y, z = vertices[:, 0], vertices[:, 1], vertices[:, 2]

        if path_model.endswith('obj'):
            # Create a 3D surface plot for faces
            mesh = go.Mesh3d(
                x=x,
                y=y,
                z=z,
                i=faces[:, 0]-1,
                j=faces[:, 1]-1,
                k=faces[:, 2]-1,
                opacity=1,
                # intensity=y,
                facecolor=face_colors,
                lighting=dict(ambient=0.8, diffuse=1, fresnel=0.2),
                colorscale='Viridis',
                )
        else:
            mesh = go.Mesh3d(
                x=x,
                y=y,
                z=z,
                i=faces[:, 0],
                j=faces[:, 1],
                k=faces[:, 2],
                opacity=1,
                # intensity=y,
                facecolor=face_colors,
                lighting=dict(ambient=0.8, diffuse=1, fresnel=0.2),
                colorscale='Viridis'
                )

    else:
        print(len(faces))
        # Extract x, y, z coordinates from vertices
        x, y, z = vertices[:, 0], vertices[:, 1], vertices[:, 2]

        if path_model.endswith('obj'):
            # Create a 3D surface plot for faces
            mesh = go.Mesh3d(
                x=x,
                y=y,
                z=z,
                i=faces[:, 0]-1,
                j=faces[:, 1]-1,
                k=faces[:, 2]-1,
                opacity=1,
                # intensity=y,
                # facecolor=face_colors,
                lighting=dict(ambient=0.8, diffuse=1, fresnel=0.2),
                colorscale='Viridis',
                )
        else:
            mesh = go.Mesh3d(
                x=x,
                y=y,
                z=z,
                i=faces[:, 0],
                j=faces[:, 1],
                k=faces[:, 2],
                opacity=1,
                # intensity=y,
                # facecolor=face_colors,
                lighting=dict(ambient=0.8, diffuse=1, fresnel=0.2),
                colorscale='Viridis'
                )

    # Create a layout
    layout = go.Layout(
        scene=dict(
            aspectmode='data',
            camera=dict(eye=dict(x=1.25, y=1.25, z=1.25)),
            xaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            yaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            zaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            
        )
    )

    # Create a figure and add the scatter and surface plots
    fig = go.Figure(data=mesh, layout=layout)
    # fig = go.Figure(data=[scatter, mesh], layout=layout)

    fig.update_layout(width=800, height=600)
    
    # Show the figure
    # fig.show()
    iplot(fig)

In [8]:
def show_point_clouds(path_model, path_label):
    
    # Load models
    if path_model.endswith('ply'):
        vertices, faces = load_ply_file(path_model)
    elif path_model.endswith('off'):
        vertices, faces = load_off_file(path_model)
    elif path_model.endswith('obj'):
        vertices, faces = read_obj_file(path_model)

    # Load labels
    
    labels = load_txt_file(path_label)
    color_scale = {
        '0': 'black',
        '1': 'red',
        '2': 'blue',
        '3': 'green',
        '4': 'yellow',
        '5': 'purple',
        '6': 'orange',
        '7': 'pink',
        '8': 'cyan'}
    face_colors = [color_scale[label] for row in labels for label in row]
    print(len(labels),len(faces))
    
    # Extract x, y, z coordinates from vertices
    x, y, z = vertices[:, 0], vertices[:, 1], vertices[:, 2]

    if path_model.endswith('obj'):
        # Create a 3D surface plot for faces
        mesh = go.Scatter3d(
                x=x,
                y=y,
                z=z,
                mode='markers',
                marker=dict(
                    size=2,
                    color='rgb(0, 0, 255)',
                    opacity=0.8
                )
            )   
    else:
        mesh = go.Scatter3d(
                x=x,
                y=y,
                z=z,
                mode='markers',
                # facecolor=face_colors,
                marker=dict(
                    size=2,
                    color='rgb(0, 0, 255)',
                    opacity=0.8
                )
            )

    # Create a layout
    layout = go.Layout(
        scene=dict(
            aspectmode='data',
            camera=dict(eye=dict(x=1.25, y=1.25, z=1.25)),
            xaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            yaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            zaxis=dict(
                showgrid=False,
                showline=False,
                showticklabels=False,
                showbackground=False,
                title='',
            ),
            
        )
    )

    # Create a figure and add the scatter and surface plots
    fig = go.Figure(data=mesh, layout=layout)
    # fig = go.Figure(data=[scatter, mesh], layout=layout)

    fig.update_layout(width=800, height=600)
    
    # Show the figure
    # fig.show()
    iplot(fig)

In [9]:
# Plot train data
path = current_path + "/data/sig17_seg_benchmark/"

# Adobe
path_model = path + "meshes/train/adobe/ToonFemaleA_tri_fixed.off"
path_label = path + "segs/train/adobe/ToonFemaleA_tri_fixed.txt"

# Faust
# path_model = path + "meshes/train/faust/tr_reg_023.ply"
# path_label = path + "segs/train/faust/faust_corrected.txt"

# MIT
# path_model = path + "meshes/train/MIT_animation/meshes_squat1/meshes/mesh_0160.obj"
# path_label = path + "segs/train/mit/mit_squat1_corrected.txt"

# Scape
# path_model = path + "meshes/train/scape/mesh015.off"
# path_label = path + "segs/train/scape/scape_corrected.txt"

show_3d_model(path_model, path_label)
show_point_clouds(path_model, path_label)

15080 15080


15080 15080


In [10]:
# Plot test data
path = current_path + "/data/sig17_seg_benchmark/"

# Schrec
input_nb = 17
path_model = path + f"meshes/test/shrec/{input_nb}.off"
path_label = path + f"segs/test/shrec/shrec_{input_nb}_full.txt"

# for i in range(1,20):
#     print(i)
#     if (i!=16) and (i!=18):
#         if i == 12:
#             path_model = path + f"meshes/test/shrec/12_fix_orientation.off"
#             path_label = path + f"segs/test/shrec/shrec_12_full.txt"
#         else :
#             path_model = path + f"meshes/test/shrec/{i}.off"
#             path_label = path + f"segs/test/shrec/shrec_{i}_full.txt"
#         show_3d_model(path_model, path_label)

show_3d_model(path_model, path_label)

In [11]:
# Plot EHF dataset
path = current_path + "/data/"
input_nb = 95
path_model = path + f"EHF_dataset/meshes/test/{input_nb}_align.ply"
path_label = path + f"EHF_dataset/segs/test/output_ehf_{input_nb}.txt"

# for i in range(1,5):
#     print(i)
#     if i<10:
#         path_model = path + f"EHF_dataset/meshes/test/0{i}_align.ply"
#         path_label = path + f"EHF_dataset/segs/test/output_ehf_{i}.txt"
#     else:
#         path_model = path + f"EHF_dataset/meshes/test/{i}_align.ply"
#         path_label = path + f"EHF_dataset/segs/test/output_ehf_{i}.txt"
#     show_3d_model(path_model, path_label)

show_3d_model(path_model, path_label)

20908 20908


In [13]:
# # Plot bearded guy
# path = current_path + "/data/"
# path_model = path + f"other_data/meshes/test/Bearded guy.ply"
# path_label = path + f"other_data/segs/test/output_0.txt"

# show_3d_model(path_model, path_label)

In [14]:
# # Plot hand
# path = current_path + "/data/"
# path_model = path + f"other_data/meshes/test/Hand.ply"
# path_label = path + f"other_data/segs/test/output_1.txt"

# show_3d_model(path_model, path_label)

### Add noise to test data models

In [21]:
def write_ply_file(vertices, faces, filename):
    # Check if the number of vertices and faces match
    if len(vertices) == 0 or len(faces) == 0:
        raise ValueError("Vertices and faces arrays must not be empty")

    num_vertices = len(vertices)
    num_faces = len(faces)

    with open(filename, 'w') as ply_file:
        # Write the PLY header
        ply_file.write("ply\n")
        ply_file.write("format ascii 1.0\n")
        ply_file.write(f"element vertex {num_vertices}\n")
        ply_file.write("property float x\n")
        ply_file.write("property float y\n")
        ply_file.write("property float z\n")
        ply_file.write(f"element face {num_faces}\n")
        ply_file.write("property list uchar int vertex_indices\n")
        ply_file.write("end_header\n")

        # Write the vertices
        for vertex in vertices:
            ply_file.write(f"{vertex[0]} {vertex[1]} {vertex[2]}\n")

        # Write the faces
        for face in faces:
            ply_file.write(f"{len(face)} {' '.join(map(str, face))}\n")

    print(f"PLY file '{filename}' successfully created.")

In [43]:
def add_noise_to_ply(input_file_path, output_file_path, noise_factor=0.01):
    # Load PLY file
    ply_data = PlyData.read(input_file_path)

    # Extract vertex data
    vertices = np.array([(vertex['x'], vertex['y'], vertex['z']) for vertex in ply_data['vertex']])

    # Apply noise to vertex coordinates
    noisy_vertices = vertices + noise_factor * np.random.randn(*vertices.shape)

    # Extract face data
    faces = np.array([list(face) for face in ply_data['face']['vertex_indices']])
    
    write_ply_file(noisy_vertices, faces, output_file_path)

In [44]:
# Create several noisy ply files
j = 1
for i in range(70,90):
    path = current_path + "/data/"
    path_model = path + f"EHF_dataset/meshes/test/{i}_align.ply"

    add_noise_to_ply(path_model, path + f"EHF_dataset/meshes/test/{j+100}_align.ply")
    j+=1

PLY file '/Users/adelemoreau/Desktop/MVA/S1/Geometric Data Analysis/Projet/diffusion-net-geometric-data-analysis/experiments/human_segmentation_original/data/EHF_dataset/meshes/test/101_align.ply' successfully created.
PLY file '/Users/adelemoreau/Desktop/MVA/S1/Geometric Data Analysis/Projet/diffusion-net-geometric-data-analysis/experiments/human_segmentation_original/data/EHF_dataset/meshes/test/102_align.ply' successfully created.
PLY file '/Users/adelemoreau/Desktop/MVA/S1/Geometric Data Analysis/Projet/diffusion-net-geometric-data-analysis/experiments/human_segmentation_original/data/EHF_dataset/meshes/test/103_align.ply' successfully created.
PLY file '/Users/adelemoreau/Desktop/MVA/S1/Geometric Data Analysis/Projet/diffusion-net-geometric-data-analysis/experiments/human_segmentation_original/data/EHF_dataset/meshes/test/104_align.ply' successfully created.
PLY file '/Users/adelemoreau/Desktop/MVA/S1/Geometric Data Analysis/Projet/diffusion-net-geometric-data-analysis/experiments

In [49]:
show_3d_model(path + f"EHF_dataset/meshes/test/{120}_align.ply", path + f"EHF_dataset/segs/test/output_ehf_{120}.txt")

20908 20908
